## Installing Pytorch

In [1]:
# http://pytorch.org/
from os.path import exists
from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())
cuda_output = !ldconfig -p|grep cudart.so|sed -e 's/.*\.\([0-9]*\)\.\([0-9]*\)$/cu\1\2/'
accelerator = cuda_output[0] if exists('/dev/nvidia0') else 'cpu'

!pip install -q http://download.pytorch.org/whl/{accelerator}/torch-0.4.1-{platform}-linux_x86_64.whl torchvision
import torch

tcmalloc: large alloc 1073750016 bytes == 0x58872000 @  0x7f207b18d2a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641


## Building Fairseq

In [2]:
!git clone https://github.com/pytorch/fairseq.git
import os
os.chdir("fairseq/")
!pip install -r requirements.txt
%run -i 'setup.py' build develop

Cloning into 'fairseq'...
remote: Enumerating objects: 31, done.
remote: Counting objects: 100% (31/31), done.
remote: Compressing objects: 100% (24/24), done.
remote: Total 3094 (delta 13), reused 8 (delta 7), pack-reused 3063
Receiving objects: 100% (3094/3094), 3.14 MiB | 15.91 MiB/s, done.
Resolving deltas: 100% (2247/2247), done.
running build
running build_py
creating build
creating build/lib.linux-x86_64-3.6
creating build/lib.linux-x86_64-3.6/tests
copying tests/test_iterators.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_noising.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_convtbc.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_dictionary.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_character_token_embedder.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_average_checkpoints.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_sequence_scorer.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_label_smoothing.

## Model for Nso

### Data

In [6]:
!git clone https://github.com/LauraMartinus/ukuxhumana.git

Cloning into 'ukuxhumana'...
remote: Enumerating objects: 6, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 1272 (delta 0), reused 4 (delta 0), pack-reused 1266
Receiving objects: 100% (1272/1272), 380.71 MiB | 21.95 MiB/s, done.
Resolving deltas: 100% (607/607), done.
Checking out files: 100% (300/300), done.


### Subword

In [4]:
!git clone https://github.com/rsennrich/subword-nmt

Cloning into 'subword-nmt'...
remote: Enumerating objects: 4, done.
remote: Counting objects: 100% (4/4), done.
remote: Compressing objects: 100% (4/4), done.
remote: Total 485 (delta 0), reused 1 (delta 0), pack-reused 481
Receiving objects: 100% (485/485), 205.64 KiB | 2.74 MiB/s, done.
Resolving deltas: 100% (287/287), done.


In [7]:
#os.chdir('../')
!ls

fairseq  sample_data  ukuxhumana


In [10]:
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt

# Learn a vocabulary using 40,000 merge operations
!fairseq/subword-nmt/learn_bpe.py -s 4000 <combine.txt> ennso.codes

# Apply the vocabulary to the training file
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='ennso.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Plea

In [0]:
os.chdir('fairseq/')

In [12]:
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

Namespace(alignfile=None, destdir='data-bin/ennso', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='en', srcdict=None, target_lang='nso', testpref='../test', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../train', validpref='../valid', workers=1)
| [en] Dictionary: 2991 types
| [en] ../train.en: 21543 sents, 672811 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 2991 types
| [en] ../valid.en: 6234 sents, 192753 tokens, 0.0223% replaced by <unk>
| [en] Dictionary: 2991 types
| [en] ../test.en: 3000 sents, 69973 tokens, 0.0171% replaced by <unk>
| [nso] Dictionary: 3415 types
| [nso] ../train.nso: 21543 sents, 738066 tokens, 0.0% replaced by <unk>
| [nso] Dictionary: 3415 types
| [nso] ../valid.nso: 6234 sents, 208039 tokens, 0.0269% replaced by <unk>
| [nso] Dictionary: 3415 types
| [nso] ../test.nso: 3000 sents, 78649 tokens, 0.0839% replaced by <unk>
| Wrote preprocessed data to data-bin/ennso

### Train Model

In [13]:
!mkdir -p chckpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir ckpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path ckpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

Namespace(arch='fconv', bucket_cap_mb=150, clip_norm=0.1, criterion='cross_entropy', data=['data-bin/ennso'], ddp_backend='c10d', decoder_attention='True', decoder_embed_dim=512, decoder_embed_path=None, decoder_layers='[(512, 3)] * 20', decoder_out_embed_dim=256, device_id=0, distributed_backend='nccl', distributed_init_method=None, distributed_port=-1, distributed_rank=0, distributed_world_size=1, dropout=0.2, encoder_embed_dim=512, encoder_embed_path=None, encoder_layers='[(512, 3)] * 20', fix_batches_to_gpus=False, fp16=False, fp16_init_scale=128, fp16_scale_tolerance=0.0, fp16_scale_window=None, keep_interval_updates=-1, left_pad_source='True', left_pad_target='False', log_format=None, log_interval=1000, lr=[0.25], lr_scheduler='reduce_lr_on_plateau', lr_shrink=0.1, max_epoch=0, max_sentences=None, max_sentences_valid=None, max_source_positions=1024, max_target_positions=1024, max_tokens=4000, max_update=0, min_loss_scale=0.0001, min_lr=1e-05, momentum=0.99, no_epoch_checkpoints=F

### Testing
Generate translations from the test data. Calculate the Bleu score.

In [0]:
# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path ckpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**8k**

In [21]:
os.chdir('../')
!ls

combine.txt  fairseq	  test.en   train.en   ukuxhumana  valid.nso
ennso.codes  sample_data  test.nso  train.nso  valid.en


In [22]:
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 8000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='ennso.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Plea

**12k**

In [24]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 12000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir chekpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path chekpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='ennso.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Plea

**16k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 16000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**20k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 20000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**24k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 24000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**28k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 28000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**32k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 32000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/enaf \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**36k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 36000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/enaf \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

**40k**

In [0]:
os.chdir('../')
!cat ukuxhumana/clean/en_nso/ennso_parallel.train.en ukuxhumana/clean/en_nso/ennso_parallel.train.nso > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 40000 <combine.txt> ennso.codes

!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ukuxhumana/clean/en_nso/ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang nso --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/enaf \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang nso

## Results

*   40k: 
*   36k: 
*   32k:
*   28k: 
*   24k: 
*   20k: 
*   16k: 
*   12k: 10.14
*     8k: 8.73
*     4k: 12.18

